# HW1 布尔查询之BSBI与索引压缩

本次作业使用斯坦福大学[CS 276 / LING 286: Information Retrieval and Web Search](https://web.stanford.edu/class/cs276/)课程的代码框架来实现。具体来说主要包含的内容有：
1. [索引构建 (40%)](#索引构建与检索-(40%)) 使用BSBI方法模拟在内存不足的情况下的索引构建方式，并应用于布尔查询
2. [索引压缩 (30%)](#索引压缩-(30%)) 使用可变长编码对构建的索引进行压缩
3. [布尔检索 (10%)](#布尔联合检索-(10%)) 对空格分隔的单词查询进行联合（与）布尔检索
3. [实验报告 (10%)](#Report-(25%)) 描述你的代码并回答一些问题
4. [额外的编码方式 (10%)](#额外的编码方式-(10%)) 鼓励使用额外的编码方式对索引进行压缩 (例如, gamma-encoding)

In [ ]:
# You can add additional imports here
import sys
import pickle as pkl
import array
import os
import timeit
import contextlib
# my import
bitarray

# 数据集

实验使用的文本数据是stanford.edu域下的网页内容，可从http://web.stanford.edu/class/cs276/pa/pa1-data.zip 下载。以下代码将大约170MB的文本数据下载到当前目录下，

In [108]:
import urllib.request
import zipfile

# data_url = "http://web.stanford.edu/class/cs276/pa/pa1-data.zip"
# data_dir = "pa1-data"
# # urllib.request.urlretrieve(data_url, data_dir + ".zip")
# zip_ref = zipfile.ZipFile(data_dir + ".zip", "r")
# zip_ref.extractall()
# zip_ref.close()

之后构建的索引会被存储到`output_dir`，`tmp`会存储测试数据（toy-data）所生成的一些临时文件

In [109]:
try:
    os.mkdir("output_dir")
except FileExistsError:
    pass
try:
    os.mkdir("tmp")
except FileExistsError:
    pass
try:
    os.mkdir("toy_output_dir")
except FileExistsError:
    pass

在数据目录下有10个子目录（命名0-9）

In [110]:
sorted(os.listdir("pa1-data"))

['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']

每一个子目录下的文件都包含一个独立网页的内容。可以认为在同一子目录下没有同名文件，即每个文件的绝对路径不会相同。

In [111]:
sorted(os.listdir("pa1-data/0"))[:10]

['3dradiology.stanford.edu_',
 '3dradiology.stanford.edu_patient_care_Case%2520studies_AVM.html',
 '3dradiology.stanford.edu_patient_care_case_studies.html',
 '5-sure.stanford.edu_',
 '50years.stanford.edu_',
 'a3cservices.stanford.edu_awards_nominate_',
 'a3cservices.stanford.edu_facilities_',
 'a3cservices.stanford.edu_lead_',
 'aa.stanford.edu_',
 'aa.stanford.edu_about_aviation.php']

所有的网页内容已经经过处理，仅包含由空格分隔开的单词，不再需要进行额外的标准化工作。

In [112]:
with open("pa1-data/0/3dradiology.stanford.edu_", "r") as f:
    print(f.read())

3d radiology lab stanford university school of medicine stanford school of medicine 3d and quantitative imaging in the department of radiology search this site only stanford medical sites ways to give find a person alumni lane library ways to give find a person about us mission to develop and apply innovative techniques for efficient quantitative analysis and display of medical imaging data through interdisciplinary collaboration goals education to train physicians and technologists locally and worldwide in the latest developments in 3d and quantitative imaging research to develop new approaches to the exploration analysis and quantitative assesment of diagnostic images that result in a new and or more cost effective diagnostic approaches and b new techniques for the design and planning and monitoring of therapy patient care to deliver valid clinically relevant visualization and analysis of medical imaging data to the stanford community locations richard m lucas magnetic resonance imag

# 索引构建与检索 (40%)

作业的第一部分是使用**blocked sort-based indexing (BSBI)** 算法来构建倒排索引并实现布尔检索。关于BSBI算法可以参考老师课件或者斯坦福教材[Section 4.2](http://nlp.stanford.edu/IR-book/pdf/04const.pdf)。以下摘自教材内容

> To construct an index, we first make a pass through the collection assembling all term-docID pairs. We then sort the pairs with the term as the dominant key and docID as the secondary key. Finally, we organize the docIDs for each term into a postings list and compute statistics like term and document frequency. For small collections, all this can be done in memory. 

对于无法在内存一次性处理的较大数据集，将会使用到二级存储（如：磁盘）。

## IdMap (6%)

再次引用教材 Section 4.2:

> To make index construction more efficient, we represent terms as termIDs (instead of strings), where each termID is a unique serial number. We can build the mapping from terms to termIDs on the fly while we are processing the collection. Similarly, we also represent documents as docIDs (instead of strings).

我们首先定义一个辅助类`IdMap`，用于将字符串和数字ID进行相互映射，以满足我们在term和termID、doc和docID间转换的需求。

实现以下代码中的`_get_str` 和 `_get_id`函数，IdMap类的唯一接口是`__getitem__`，它是一个特殊函数，重写了下标运算`[]`,根据下标运算键的类型得到正确的映射值（如果不存在需要添加）。（特殊函数可参考[官方文档](https://docs.python.org/3.7/reference/datamodel.html#special-method-names)）
<br>
<br>
我们会用到字典来将字符串转换为数字，用列表来将数字转换为字符串。(4%)

In [113]:
class IdMap:
    """Helper class to store a mapping from strings to ids."""

    def __init__(self):
        self.str_to_id = {}
        self.id_to_str = []

    def __len__(self):
        """Return number of terms stored in the IdMap"""
        
        return len(self.id_to_str)

    def _get_str(self, i):
        """Returns the string corresponding to a given id (`i`)."""
        ### Begin your code
        return self.id_to_str[i]
        ### End your code

    def _get_id(self, s):
        """Returns the id corresponding to a string (`s`).
        If `s` is not in the IdMap yet, then assigns a new id and returns the new id.
        """
        ### Begin your code
        if s not in self.str_to_id:
            self.id_to_str.append(s)
            self.str_to_id[s] = len(self.id_to_str) - 1
        return self.str_to_id[s]
        ### End your code

    def __getitem__(self, key):
        """If `key` is a integer, use _get_str;
        If `key` is a string, use _get_id;"""
        if type(key) is int:
            return self._get_str(key)
        elif type(key) is str:
            return self._get_id(key)
        else:
            raise TypeError

确保代码能通过以下简单测试样例 (2%)

In [114]:
testIdMap = IdMap()

assert testIdMap["a"] == 0, "Unable to add a new string to the IdMap"
assert testIdMap["bcd"] == 1, "Unable to add a new string to the IdMap"
assert testIdMap["a"] == 0, "Unable to retrieve the id of an existing string"
assert (
    testIdMap[1] == "bcd"
), "Unable to retrive the string corresponding to a\
                                given id"
try:
    testIdMap[2]
except IndexError as e:
    assert True, "Doesn't throw an IndexError for out of range numeric ids"
assert len(testIdMap) == 2

之后会需要你自己来写测试样例来确保你的程序正常运行

## 将倒排列表编码成字节数组 (2%)

为了高效地从磁盘读写倒排列表（文档ID），我们将其存储为字节数组的形式。代码提供了`UncompressedPostings`类来用静态函数实现对倒排列表的编码和解码。在之后的任务中你需要使用该接口实现索引压缩版本（可变长编码）。

参考:
1. https://docs.python.org/3/library/array.html
2. https://pymotw.com/3/array/#module-array

In [115]:
class UncompressedPostings:

    @staticmethod
    def encode(postings_list):
        """Encodes postings_list into a stream of bytes

        Parameters
        ----------
        postings_list: List[int]
            List of docIDs (postings)

        Returns
        -------
        bytes
            bytearray representing integers in the postings_list
        """
        return array.array("L", postings_list).tobytes()

    @staticmethod
    def decode(encoded_postings_list):
        """Decodes postings_list from a stream of bytes

        Parameters
        ----------
        encoded_postings_list: bytes
            bytearray representing encoded postings list as output by encode
            function

        Returns
        -------
        List[int]
            Decoded list of docIDs from encoded_postings_list
        """

        decoded_postings_list = array.array("L")
        decoded_postings_list.frombytes(encoded_postings_list)
        return decoded_postings_list.tolist()

运行以下代码查看其工作方式 (2%)

In [116]:
x = UncompressedPostings.encode([1, 2, 3])
print(x)
print(UncompressedPostings.decode(x))

b'\x01\x00\x00\x00\x02\x00\x00\x00\x03\x00\x00\x00'
[1, 2, 3]


## 磁盘上的倒排索引 (2%)

> With main memory insufficient, we need to use an external sorting algorithm, that is, one that uses disk. For acceptable speed, the central requirement of such an algorithm is that it minimize the number of random disk seeks during sorting - sequential disk reads are far faster than seeks. 

在这一部分我们提供了一个基类`InvertedIndex`，之后会在此基础上构建它的子类`InvertedIndexWriter`, `InvertedIndexIterator` 和 `InvertedIndexMapper`。在Python中我们常用`cPickle`进行序列化，但是它并不支持部分读和部分写，无法满足BSBI算法的需要，所以我们需要定义自己的存储方式。

In [117]:
class InvertedIndex:
    """A class that implements efficient reads and writes of an inverted index
    to disk

    Attributes
    ----------
    postings_dict: Dictionary mapping: termID->(start_position_in_index_file,
                                                number_of_postings_in_list,
                                               length_in_bytes_of_postings_list)
        This is a dictionary that maps from termIDs to a 3-tuple of metadata
        that is helpful in reading and writing the postings in the index file
        to/from disk. This mapping is supposed to be kept in memory.
        start_position_in_index_file is the position (in bytes) of the postings
        list in the index file
        number_of_postings_in_list is the number of postings (docIDs) in the
        postings list
        length_in_bytes_of_postings_list is the length of the byte
        encoding of the postings list

    terms: List[int]
        A list of termIDs to remember the order in which terms and their
        postings lists were added to index.

        After Python 3.7 we technically no longer need it because a Python dict
        is an OrderedDict, but since it is a relatively new feature, we still
        maintain backward compatibility with a list to keep track of order of
        insertion.
    """

    def __init__(self, index_name, postings_encoding=None, directory=""):
        """
        Parameters
        ----------
        index_name (str): Name used to store files related to the index
        postings_encoding: A class implementing static methods for encoding and
            decoding lists of integers. Default is None, which gets replaced
            with UncompressedPostings
        directory (str): Directory where the index files will be stored
        """

        self.index_file_path = os.path.join(directory, index_name + ".index")
        self.metadata_file_path = os.path.join(directory, index_name + ".dict")

        if postings_encoding is None:
            self.postings_encoding = UncompressedPostings
        else:
            self.postings_encoding = postings_encoding
        self.directory = directory

        self.postings_dict = {}
        self.terms = []  # Need to keep track of the order in which the
        # terms were inserted. Would be unnecessary
        # from Python 3.7 onwards

    def __enter__(self):
        """Opens the index_file and loads metadata upon entering the context"""
        # Open the index file
        self.index_file = open(self.index_file_path, "rb+")

        # Load the postings dict and terms from the metadata file
        with open(self.metadata_file_path, "rb") as f:
            self.postings_dict, self.terms = pkl.load(f)
            self.term_iter = self.terms.__iter__()

        return self

    def __exit__(self, exception_type, exception_value, traceback):
        """Closes the index_file and saves metadata upon exiting the context"""
        # Close the index file
        self.index_file.close()

        # Write the postings dict and terms to the metadata file
        with open(self.metadata_file_path, "wb") as f:
            pkl.dump([self.postings_dict, self.terms], f)

因为是在与磁盘上的文件进行交互，所以我们提供了`__enter__`和`__exit__`函数，它使得我们能够像使用python中文件IO一样使用`with`语句。（参考[上下文管理器官方文档](https://docs.python.org/3/library/contextlib.html)）

以下是使用 `InvertedIndexWriter` 上下文管理器的实例: (2%)

```python
with InvertedIndexWriter('test', directory='tmp/') as index:
    # Some code here
```

## 索引 (30%)

> BSBI (i) segments the collection into parts of equal size, (ii) sorts the termID-docID pairs of each part in memory, (iii) stores intermediate sorted results on disk, and (iv) merges all intermediate results into the final index. 

你需要将每一个子目录当做一个块（block），并且在构建索引的过程中每次只能加载一个块（模拟内存不足）。注意到我们是将操作系统意义上的块进行了抽象。你可以认为每个块足够小，能被装载进内存。

在这一部分，我们将阶段性地构造类`BSBIIndex`。函数`index`给出了BSBI算法的框架，而你的工作则是在接下来的部分中实现函数`parse_block`, `invert_write` 和 `merge`。

In [118]:
# Do not make any changes here, they will be overwritten while grading
class BSBIIndex:
    """
    Attributes
    ----------
    term_id_map(IdMap): For mapping terms to termIDs
    doc_id_map(IdMap): For mapping relative paths of documents (eg
        0/3dradiology.stanford.edu_) to docIDs
    data_dir(str): Path to data
    output_dir(str): Path to output index files
    index_name(str): Name assigned to index
    postings_encoding: Encoding used for storing the postings.
        The default (None) implies UncompressedPostings
    """

    def __init__(self, data_dir, output_dir, index_name="BSBI", postings_encoding=None):
        self.term_id_map = IdMap()
        self.doc_id_map = IdMap()
        self.data_dir = data_dir
        self.output_dir = output_dir
        self.index_name = index_name
        self.postings_encoding = postings_encoding

        # Stores names of intermediate indices
        self.intermediate_indices = []

    def save(self):
        """Dumps doc_id_map and term_id_map into output directory"""

        with open(os.path.join(self.output_dir, "terms.dict"), "wb") as f:
            pkl.dump(self.term_id_map, f)
        with open(os.path.join(self.output_dir, "docs.dict"), "wb") as f:
            pkl.dump(self.doc_id_map, f)

    def load(self):
        """Loads doc_id_map and term_id_map from output directory"""

        with open(os.path.join(self.output_dir, "terms.dict"), "rb") as f:
            self.term_id_map = pkl.load(f)
        with open(os.path.join(self.output_dir, "docs.dict"), "rb") as f:
            self.doc_id_map = pkl.load(f)

    def index(self):
        """Base indexing code

        This function loops through the data directories,
        calls parse_block to parse the documents
        calls invert_write, which inverts each block and writes to a new index
        then saves the id maps and calls merge on the intermediate indices
        """
        for block_dir_relative in sorted(next(os.walk(self.data_dir))[1]):
            td_pairs = self.parse_block(block_dir_relative)
            index_id = "index_" + block_dir_relative
            self.intermediate_indices.append(index_id)
            with InvertedIndexWriter(
                index_id,
                directory=self.output_dir,
                postings_encoding=self.postings_encoding,
            ) as index:
                self.invert_write(td_pairs, index)
                td_pairs = None
        self.save()
        with InvertedIndexWriter(
            self.index_name,
            directory=self.output_dir,
            postings_encoding=self.postings_encoding,
        ) as merged_index:
            with contextlib.ExitStack() as stack:
                indices = [
                    stack.enter_context(
                        InvertedIndexIterator(
                            index_id,
                            directory=self.output_dir,
                            postings_encoding=self.postings_encoding,
                        )
                    )
                    for index_id in self.intermediate_indices
                ]
                self.merge(indices, merged_index)

### 解析 (10%)

> The function `parse_block`  parses documents into termID-docID pairs and accumulates the pairs in memory until a block of a fixed size is full. We choose the block size to fit comfortably into memory to permit a fast in-memory sort. 

你需要将每一个子目录当做一个块，`parse_block`接收子目录路径作为参数。同一子目录下所有文件名都是不同的。 (5%)

_注意 - 我们使用 `BSBIIndex` 继承 `BSBIIndex`, 这只是对一个已存在类添加新内容的简单方法。在这里只是用来切分类的定义（jupyter notebook内教学使用，无特殊含义）。_

In [119]:
class BSBIIndex(BSBIIndex):
    def parse_block(self, block_dir_relative):
        """Parses a tokenized text file into termID-docID pairs

        Parameters
        ----------
        block_dir_relative : str
            Relative Path to the directory that contains the files for the block

        Returns
        -------
        List[Tuple[Int, Int]]
            Returns all the td_pairs extracted from the block

        Should use self.term_id_map and self.doc_id_map to get termIDs and docIDs.
        These persist across calls to parse_block
        """
        ### Begin your code
        #TODO 可能出现的问题,  td_pairs sorted 之后是否
        # 在相同term_id 下, 关于 term_id 升序, 在inverted_write 部分有说.
        # 感觉按这里的获取td_pairs 的方式 ,是有这样的性质
        block_path = os.path.join(self.data_dir, block_dir_relative)
        td_pairs = []
        for filename in os.listdir(block_path):
            #BUG 到布尔检索那里才知道 要存路径。。。不过想想也是，应该存
            doc_id = self.doc_id_map[os.path.join(block_dir_relative,filename)]
            filepath = os.path.join(block_path, filename)
            unique_term_id = set()
            with open(filepath, 'r', encoding='utf-8') as f:
                words = f.read().split()
                for word in words:
                    term_id = self.term_id_map[word]
                    # not in 一个列表会是 O(n)的,
                    # 所以我之前这样去重，复杂度至少O(n^2)
                    # if (term_id, doc_id) not in td_pairs: #TODO 似乎不需要存词频，所以要去重
                    #     td_pairs.append((term_id, doc_id))
                    # 由于是一个个文件处理的，所以doc_id 是一样的
                    unique_term_id.add(term_id)
            # 转换然后给td_pairs 
            td_pairs += [(key, doc_id) for key in unique_term_id]
        return  td_pairs
        ### End your code

观察函数在测试数据上是否正常运行 (2%)

In [120]:
data_dir = "toy-data"
output_dir = "output_dir"
# actual_data_path = os.path.abspath(data_dir)
# print(f"实际路径 {actual_data_path}") 

with open("toy-data/0/fine.txt", "r") as f:
    print(f.read())
    # f.seek(0)
    # print(f.read())
with open("toy-data/0/hello.txt", "r") as f:
    print(f.read())
    
    
testBSBI_parse_block = BSBIIndex(data_dir, output_dir)
print(testBSBI_parse_block.parse_block("0")) # 有标点没关系。。实际用的文档是全部以空格隔开的
# print(f"有什么呢：\n{testBSBI_parse_block.term_id_map.id_to_str}")
print(testBSBI_parse_block.doc_id_map.str_to_id)
print(testBSBI_parse_block.term_id_map.str_to_id)

i'm fine , thank you

hi hi
how are you ?

[(0, 0), (1, 0), (2, 0), (3, 0), (4, 0), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1)]
{'0\\fine.txt': 0, '0\\hello.txt': 1}
{"i'm": 0, 'fine': 1, ',': 2, 'thank': 3, 'you': 4, 'hi': 5, 'how': 6, 'are': 7, '?': 8}


In [121]:
toy_dir = "toy-data"
current_dir = os.getcwd()
print("当前工作目录:", current_dir)
print(os.path.join(toy_dir, "0"))

当前工作目录: d:\1Learningoutput\Year2_Part2\Information_Retrieval\hw1
toy-data\0


In [122]:
BSBI_instance = BSBIIndex(data_dir=toy_dir, output_dir="tmp/", index_name="toy")
BSBI_instance.parse_block("0")

[(0, 0),
 (1, 0),
 (2, 0),
 (3, 0),
 (4, 0),
 (4, 1),
 (5, 1),
 (6, 1),
 (7, 1),
 (8, 1)]

写一些测试样例来确保`parse_block`方法正常运行（如：相同单词出现时是相同ID） (3%)

In [123]:
### Begin your code
#TODO 累的时候写，似乎我得弄个文件夹或者文件来存吧？毕竟只能从文件里读欸
### End your code

### 倒排表 (10%)

> The block is then inverted and written to disk. Inversion involves two steps. First, we sort the termID-docID pairs. Next, we collect all termID-docID pairs with the same termID into a postings list, where a posting is simply a docID. The result, an inverted index for the block we have just read, is then written to disk.

在这一部分我们添加函数`invert_write`来实现由termID-docID对构建倒排表。 

但是，我们首先需要实现类`InvertedIndexWriter`。和列表类似，该类提供了append函数，但是倒排表不会存储在内存中而是直接写入到磁盘里。 (3%)

In [124]:
class InvertedIndexWriter(InvertedIndex):
    """"""

    def __enter__(self):
        self.index_file = open(self.index_file_path, "wb+")
        return self

    def append(self, term, postings_list):
        """Appends the term and postings_list to end of the index file.

        This function does three things,
        1. Encodes the postings_list using self.postings_encoding
        2. Stores metadata in the form of self.terms and self.postings_dict
           Note that self.postings_dict maps termID to a 3 tuple of
           (start_position_in_index_file,
           number_of_postings_in_list,
           length_in_bytes_of_postings_list)
        3. Appends the bytestream to the index file on disk

        Hint: You might find it helpful to read the Python I/O docs
        (https://docs.python.org/3/tutorial/inputoutput.html) for
        information about appending to the end of a file.

        Parameters
        ----------
        term:
            term or termID is the unique identifier for the term
        postings_list: List[Int]
            List of docIDs where the term appears
        """
        ### Begin your code
        postings_list_encoded = self.postings_encoding.encode(postings_list)
        num_of_postings = len(postings_list)
        len_in_bytes = len(postings_list_encoded)
        #TODO 如果给的是term str 而不是ID int 该怎么办？
        self.terms.append(term)
        if not self.postings_dict:
            self.postings_dict[term] = (0, num_of_postings, len_in_bytes)
        else:
            last_values = next(reversed(self.postings_dict.values())) 
            start_pos = last_values[0] + last_values[2]
            self.postings_dict[term] = (start_pos, num_of_postings, len_in_bytes)
        self.index_file.write(postings_list_encoded)
        ### End your code

In [125]:
# for my test
with InvertedIndexWriter("test", directory="tmp/") as index:
    index.append(1, [2, 3, 4])
    index.append(2, [3, 4, 5])
    print(index.postings_dict)
    

{1: (0, 3, 12), 2: (12, 3, 12)}


尽管还没有实现读取索引的类，我们还是可以用以下测试代码检测我们的实现。 (2%)

In [126]:
with InvertedIndexWriter("test", directory="tmp/") as index:
    index.append(1, [2, 3, 4])
    index.append(2, [3, 4, 5])
    index.index_file.seek(0)
    assert index.terms == [1, 2], "terms sequence incorrect"
    assert index.postings_dict == {
        1: (0, 3, len(UncompressedPostings.encode([2, 3, 4]))),
        2: (
            len(UncompressedPostings.encode([2, 3, 4])),
            3,
            len(UncompressedPostings.encode([3, 4, 5])),
        ),
    }, "postings_dict incorrect"
    assert UncompressedPostings.decode(index.index_file.read()) == [
        2,
        3,
        4,
        3,
        4,
        5,
    ], "postings on disk incorrect"

现在我们实现 `invert_write`，它将解析得到的td_pairs转换成倒排表，并使用`InvertedIndexWriter` 类将其写入磁盘。 (3%)

In [127]:
class BSBIIndex(BSBIIndex):
    def invert_write(self, td_pairs, index):
        """Inverts td_pairs into postings_lists and writes them to the given index

        Parameters
        ----------
        td_pairs: List[Tuple[Int, Int]]
            List of termID-docID pairs
        index: InvertedIndexWriter
            Inverted index on disk corresponding to the block
        """
        ### Begin your code
        #TODO 如果没有元素。。。。后面的td_pairs[0][0]会有问题吧
        if not td_pairs:
            return
        #TODO 或许不该叫TODO， td_pairs 排序后， 每个词项对应的文档被放在一起了
        # 似乎对于每个词项id， 文档id 是升序的: 
        # 原来parse的时候,从列表首到尾,是按doc_id 升序的 
        # 然后sorted 说是稳定排序,也就是说由于根据term_id 排序,
        # 对于同一个 term_id, 原来在右边(doc_id大), 现在还在右边.
        td_pairs = sorted(td_pairs, key=lambda pair: pair[0])
        #TODO 也许不用再创建一个列表 
        # td_pairs.sort(key = lambda pair: pair[0])
        cur_term = td_pairs[0][0] 
        cur_postings_list = []
        for pair in td_pairs:
            if pair[0] != cur_term:
                index.append(cur_term, cur_postings_list)
                cur_term = pair[0]
                cur_postings_list = []
            cur_postings_list.append(pair[1])
        index.append(cur_term, cur_postings_list)
        ### End your code

我们可以在测试数据上读取一个块并观察倒排索引中包含的内容。
仿照`InvertedIndexWriter`部分写一些测试样例。 (2%)

In [128]:
### Begin your code
#TODO 待完善与检查
# 设计好多 类， 不方便测试 啊
data_dir = "toy-data"
output_dir = "output_dir"
test_invert_write = BSBIIndex(data_dir, output_dir)
index_name = "test_invert_write"
with InvertedIndexWriter(index_name, directory="tmp/") as index:
    td_pairs = [    
        [1, 2], [4, 2], [2, 3], [1, 3], [1, 4], 
    ]
    test_invert_write.invert_write(td_pairs,index)
    assert index.terms == [1,2,4]
    print(sorted(td_pairs, key=lambda pair: pair[0]))
    print(index.terms)
    print(index.postings_dict)
    
with open(f"tmp/{index_name}.index", 'rb') as f:
    content = f.read()
    content = UncompressedPostings.decode(content)
    print(content)


# 这是用 pickle 存的，直接打开来看没意义
# with open(f"tmp/{index_name}.dict", 'rb') as f:
#     content = f.read()
#     content = UncompressedPostings.decode(content)
#     print(content)

# with InvertedIndex(index_name, directory="tmp/") as index:
#     print(index.terms)
#     print(index.postings_dict)

# test_invert_write2 = BSBIIndex(data_dir, output_dir)


### End your code

[[1, 2], [1, 3], [1, 4], [2, 3], [4, 2]]
[1, 2, 4]
{1: (0, 3, 12), 2: (12, 1, 4), 4: (16, 1, 4)}
[2, 3, 4, 3, 2]


### 合并 (10%)
> The algorithm simultaneously merges the ten blocks into one large merged index. To do the merging, we open all block files simultaneously, and maintain small read buffers for the ten blocks we are reading and a write buffer for the final merged index we are writing. 

Python中的迭代模型非常自然地符合我们维护一个小的读缓存的要求。我们可以迭代地从磁盘上每次读取文件的一个倒排列表。我们通过构建`InvertedIndex`的子类`InvertedIndexIterator`来完成这个迭代任务。 (3%)

In [129]:
class InvertedIndexIterator(InvertedIndex):
    """"""

    def __enter__(self):
        """Adds an initialization_hook to the __enter__ function of super class"""
        super().__enter__()
        self._initialization_hook()
        return self

    def _initialization_hook(self):
        """Use this function to initialize the iterator"""
        ### Begin your code
        #TODO 说是postings_dict 已经有序了, 我先试着不适用terms
        # next(self.term_iter)
        self.postings_dict_iter = self.postings_dict.items().__iter__()
        self.index_file.seek(0)
        ### End your code

    def __iter__(self):
        return self

    def __next__(self):
        """Returns the next (term, postings_list) pair in the index.

        Note: This function should only read a small amount of data from the
        index file. In particular, you should not try to maintain the full
        index file in memory.
        """
        ### Begin your code
        #TODO 也许不该用todo ， 注意返回的是 ID 而不是str
        nex_term, term_metadata = next(self.postings_dict_iter)
        #TODO 也许这个seek 可以去掉？每次read之后指针自己会变
        self.index_file.seek(term_metadata[0])
        postings_list_bytes = self.index_file.read(term_metadata[2])
        
        postings_list = self.postings_encoding.decode(postings_list_bytes)
        return (nex_term, postings_list)
        ### End your code

    def delete_from_disk(self):
        """Marks the index for deletion upon exit. Useful for temporary indices"""
        self.delete_upon_exit = True

    def __exit__(self, exception_type, exception_value, traceback):
        """Delete the index file upon exiting the context along with the
        functions of the super class __exit__ function"""
        self.index_file.close()
        if hasattr(self, "delete_upon_exit") and self.delete_upon_exit:
            os.remove(self.index_file_path)
            os.remove(self.metadata_file_path)
        else:
            with open(self.metadata_file_path, "wb") as f:
                pkl.dump([self.postings_dict, self.terms], f)

为了测试以上代码，我们先用`InvertedIndexWriter` 创建索引，然后再迭代遍历。写一些小的测试样例观察它是否正常运行。至少你得写一个测试，手工构建一个小的索引，用`InvertedIndexWriter`将他们写入磁盘，然后用`InvertedIndexIterator`迭代遍历倒排索引。 (2%)

In [130]:
### Begin your code
#TODO 待完善与检查
data_dir = "toy-data"
output_dir = "output_dir"
test_index_iter = BSBIIndex(data_dir, output_dir)
index_name = "test_index_iter"
with InvertedIndexWriter(index_name, directory="tmp/") as index:
    td_pairs = [    
        [1, 2], [4, 2], [2, 3], [1, 3], [1, 4], [4,5],[2,5], [2,10]
    ]
    test_index_iter.invert_write(td_pairs,index)
    assert index.terms == [1,2,4]
    print(sorted(td_pairs, key=lambda pair: pair[0]))
    print(index.terms)
    print(index.postings_dict)
    
with InvertedIndexIterator(index_name, directory="tmp/") as index:
    # all_postings = index.postings_encoding.decode(index.index_file.read())
    # print(all_postings)
    #TODO 似乎不应该叫TODO。在这里才找出invert_write 里的一个写错的地方
    # 说明每个函数写完之后，不要偷懒。。。应该写点测试，至少是print语句，
    # 验证写对了。
    assert next(index)== (1, [2,3,4]),"termid 1 incorrect"
    assert next(index) == (2, [3, 5, 10]), "termid 2 incorrect"
    assert next(index) == (4, [2, 5]), "termid 3 incorrect"
    try:
        next(index)
    except StopIteration:
        pass
    else: 
        assert False, "should not have more terms"
    


### End your code

[[1, 2], [1, 3], [1, 4], [2, 3], [2, 5], [2, 10], [4, 2], [4, 5]]
[1, 2, 4]
{1: (0, 3, 12), 2: (12, 3, 12), 4: (24, 2, 8)}


> During merging, in each iteration, we select the lowest termID that has not been processed yet using a priority queue or a similar data structure. All postings lists for this termID are read and merged, and the merged list is written back to disk. Each read buffer is refilled from its file when necessary.

我们将使用`InvertedIndexIterator`来完成读取的部分，用`InvertedIndexWriter`来将合并后的索引写入磁盘。

注意到我们之前一直使用`with` 语句来打开倒排索引文件，但是现在需要程序化地完成这项工作。可以看到我们在基类`BSBIIndex`的`index`函数中使用了`contextlib`([参考文档](https://docs.python.org/3/library/contextlib.html#contextlib.ExitStack))
你的任务是合并*打开的*`InvertedIndexIterator`对象（倒排列表），并且通过一个`InvertedIndexWriter`对象每次写入一个文档列表。

既然我们知道文档列表已经排过序了，那么我们可以在线性时间内对它们进行合并排序。事实上`heapq`([参考文档](https://docs.python.org/3.0/library/heapq.html)) 是Python中一个实现了堆排序算法的标准模板。另外它还包含一个实用的函数`heapq.merge`，可以将多个已排好序的输入（可迭代）合并成一个有序的输出并返回它的迭代器。它不仅可以用来合并倒排列表，也可以合并倒排索引词典。

为了让你快速上手`heapq.merge`函数，我们提供了一个简单的使用样例。给出两个以动物和树平均寿命排序的列表，我们希望合并它们。

In [131]:
import heapq

animal_lifespans = [
    ("Giraffe", 28),
    ("Rhinoceros", 40),
    ("Indian Elephant", 70),
    ("Golden Eagle", 80),
    ("Box turtle", 123),
]

tree_lifespans = [
    ("Gray Birch", 50),
    ("Black Willow", 70),
    ("Basswood", 100),
    ("Bald Cypress", 600),
]

lifespan_lists = [animal_lifespans, tree_lifespans]

for merged_item in heapq.merge(*lifespan_lists, key=lambda x: x[1]):
    print(merged_item)

('Giraffe', 28)
('Rhinoceros', 40)
('Gray Birch', 50)
('Indian Elephant', 70)
('Black Willow', 70)
('Golden Eagle', 80)
('Basswood', 100)
('Box turtle', 123)
('Bald Cypress', 600)


注意使用`*`将`lifespan_lists`解包作为参数，并且使用`lambda`函数来给出进行排序的key。如果你对它们不熟悉可以参考文档([unpacking lists](https://docs.python.org/3/tutorial/controlflow.html#unpacking-argument-lists), [lambda expressions](https://docs.python.org/3/tutorial/controlflow.html#lambda-expressions))。 (3%)

In [132]:
import heapq


class BSBIIndex(BSBIIndex):
    def merge(self, indices, merged_index):
        """Merges multiple inverted indices into a single index

        Parameters
        ----------
        indices: List[InvertedIndexIterator]
            A list of InvertedIndexIterator objects, each representing an
            iterable inverted index for a block
        merged_index: InvertedIndexWriter
            An instance of InvertedIndexWriter object into which each merged
            postings list is written out one at a time
        """
        ### Begin your code
        # 维护一个list用来存？
        # 然后每次把最小的词项。。。弄出来？ 直到所有弄完？
        # 好吧， heapq.merge就是干这个事情的
        cur_term = 0
        cur_postings = []
        for merged_item in heapq.merge(*indices): # 这里有term_id 吧？
            if merged_item[0] != cur_term:
                merged_index.append(cur_term, cur_postings)
                # 由于每个存到 termidmap 里的都是有term-doc pair的词， 编号是相邻的
                # 好吧，用 merged_item[0] 更保险
                #BUG FIX 写成+= 了，怪不得少了很多键
                cur_term = merged_item[0] # merged_item 没有了自然会停，不是无限循环
                cur_postings = []
            cur_postings += merged_item[1] # merged_item[1] 是一个 list 
        merged_index.append(cur_term, cur_postings) # 没东西了，也要存一下
        
        ### End your code

首先确保它在测试数据上正常运行

In [133]:
BSBI_instance = BSBIIndex(
    data_dir=toy_dir,
    output_dir="toy_output_dir",
)
BSBI_instance.index()

In [134]:
### my test
with InvertedIndexIterator("BSBI", directory="./toy_output_dir/") as index:
    print(index.postings_dict)
    print(index.terms)

{0: (0, 2, 8), 1: (8, 2, 8), 2: (16, 3, 12), 3: (28, 2, 8), 4: (36, 5, 20), 5: (56, 2, 8), 6: (64, 2, 8), 7: (72, 2, 8), 8: (80, 3, 12), 9: (92, 1, 4), 10: (96, 1, 4), 11: (100, 1, 4), 12: (104, 2, 8), 13: (112, 1, 4)}
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13]


接下来对整个数据集构建索引 (2%)

In [135]:
BSBI_instance = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir",
)
BSBI_instance.index()

如果你在合并阶段出现了错误，可以利用以下代码来debug。

In [136]:
BSBI_instance = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir",
)
BSBI_instance.intermediate_indices = ["index_" + str(i) for i in range(10)]
with InvertedIndexWriter(
    BSBI_instance.index_name,
    directory=BSBI_instance.output_dir,
    postings_encoding=BSBI_instance.postings_encoding,
) as merged_index:
    with contextlib.ExitStack() as stack:
        indices = [
            stack.enter_context(
                InvertedIndexIterator(
                    index_id,
                    directory=BSBI_instance.output_dir,
                    postings_encoding=BSBI_instance.postings_encoding,
                )
            )
            for index_id in BSBI_instance.intermediate_indices
        ]
        BSBI_instance.merge(indices, merged_index)

## 布尔联合检索 (10%)

我们将实现BSBIIndex中的`retrieve`函数，对于给定的包含由空格分隔tokens的字符串查询，返回包含查询中所有tokens的文档列表。但是我们并不能迭代遍历整个索引或者将整个索引加载到内存来寻找相应的terms（索引太大）。

首先我们要实现`InvertedIndex`的子类`InvertedIndexMapper`，它能够找到对应terms在索引文件中位置并取出它的倒排记录表。 (2%)

In [137]:
class InvertedIndexMapper(InvertedIndex):
    def __getitem__(self, key):
        return self._get_postings_list(key)

    def _get_postings_list(self, term):
        """Gets a postings list (of docIds) for `term`.

        This function should not iterate through the index file.
        I.e., it should only have to read the bytes from the index file
        corresponding to the postings list for the requested term.
        """
        ### Begin your code
        #TODO 这个term 应该是termid吧，因为map 在BSBI里面，InvertedIndex里用不了
        start_pos, _, len_in_bytes = self.postings_dict[term]
        self.index_file.seek(start_pos)
        postings_list_in_bytes = self.index_file.read(len_in_bytes)
        return self.postings_encoding.decode(postings_list_in_bytes)
        ### End your code

写一些测试样例检测`_get_postings_list`的实现 (1%)

In [138]:
### Begin your code
with InvertedIndexMapper("BSBI", directory="output_dir") as index:
    print(index._get_postings_list(3))

### End your code

[0, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 80, 81, 85, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 134, 143, 145, 146, 147, 148, 158, 170, 172, 182, 184, 189, 190, 191, 192, 193, 194, 195, 196, 197, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221, 222, 223, 232, 233, 234, 235, 236, 237, 238, 239, 240, 241, 242, 243, 244, 245, 246, 247, 248, 249, 250, 251, 252, 253, 254, 255, 256, 257, 258, 259, 260, 261, 262, 263, 264, 265, 266, 267, 268, 269, 270, 271, 272, 273, 274, 275, 276, 277, 278, 279, 280, 281, 282, 283, 284, 285, 286, 287, 288, 289, 290

现在我们获得了查询中terms对应的倒排记录表，接着需要求他们的交集。这部分与我们之前作业的merge方法类似，请实现`sorted_intersect`函数，遍历两个有序列表并在线性时间内合并。 (2%)

In [139]:
def sorted_intersect(list1, list2):
    """Intersects two (ascending) sorted lists and returns the sorted result

    Parameters
    ----------
    list1: List[Comparable]
    list2: List[Comparable]
        Sorted lists to be intersected

    Returns
    -------
    List[Comparable]
        Sorted intersection
    """
    ### Begin your code
    merged = heapq.merge(list1, list2)
    result = []
    seen = set()
    for doc_id in merged:
        if doc_id not in seen:
            seen.add(doc_id)
            result.append(doc_id)
    return result
    ### End your code

简单的测试样例 (1%)

In [140]:
### Begin your code
#TODO 尝试一下directory="./toy_output_dir/" 
# 与 directory="toy_output_dir" 有没有区别
# 似乎就是看看 os.path.join 有没有那么多判断逻辑？？
with InvertedIndexMapper("BSBI",directory="output_dir") as index:
    list1 = index._get_postings_list(0)
    list2 = index._get_postings_list(2)
    simple_merge_result = sorted(set(list1 + list2))
    print(simple_merge_result)
    assert simple_merge_result == sorted_intersect(list1,list2),"not equal"
    
### End your code

[0, 1, 2, 8, 9, 10, 11, 12, 30, 52, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 92, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 112, 113, 114, 115, 116, 204, 213, 252, 253, 254, 255, 256, 257, 258, 259, 260, 261, 262, 263, 264, 265, 266, 267, 268, 269, 270, 271, 272, 273, 274, 275, 276, 277, 278, 279, 280, 281, 282, 283, 284, 285, 286, 287, 288, 289, 290, 291, 292, 293, 294, 295, 296, 297, 298, 299, 300, 301, 303, 310, 314, 393, 398, 399, 411, 412, 413, 414, 415, 416, 417, 418, 419, 420, 421, 422, 423, 424, 425, 426, 427, 464, 530, 563, 579, 583, 601, 605, 620, 621, 622, 623, 631, 641, 710, 712, 714, 716, 717, 719, 732, 733, 744, 745, 746, 750, 751, 752, 761, 786, 810, 818, 838, 843, 852, 895, 972, 973, 974, 975, 976, 977, 978, 979, 981, 982, 983, 984, 985, 986, 987, 988, 989, 990, 991, 992, 994, 996, 997, 998, 999, 1000, 1001, 1020, 1137, 1722, 1931, 2008, 2016, 2219, 2580, 2620, 2636, 2680, 2681, 2682, 2683, 2684, 2685, 2686, 2711, 2716, 2773, 2

现在可以利用`sorted_intersect` 和 `InvertedIndexMapper`来实现`retrieve`函数。 (3%)

In [141]:
# %%tee submission/retrieve.py
#TODO 上面这个是什么？
class BSBIIndex(BSBIIndex):
    def retrieve(self, query:str):
        """Retrieves the documents corresponding to the conjunctive query
        
        Parameters
        ----------
        query: str
            Space separated list of query tokens
            
        Result
        ------
        List[str]
            Sorted list of documents which contains each of the query tokens. 
            Should be empty if no documents are found.
        
        Should NOT throw errors for terms not in corpus
        """
        if len(self.term_id_map) == 0 or len(self.doc_id_map) == 0:
            self.load()

        ### Begin your code
        with InvertedIndexMapper(self.index_name, self.postings_encoding, directory=self.output_dir) as index:
            # print(query.split())
            # print(list(index.postings_dict.items())[:10])
            words_id_list = [self.term_id_map[word] for word in query.split()]
            print(words_id_list)
            retrieve_lists = [index[word_id] for word_id in words_id_list]
            retrieve_lists.sort(key=lambda x:len(x))
            print(retrieve_lists)
            result = retrieve_lists[0] # 从最短的开始。。。 不过这样真的会快吗，我前面用了一个排序.
            for i in range(1,len(retrieve_lists)):
                result = sorted_intersect(result, retrieve_lists[i])
        return [self.doc_id_map[doc_id] for doc_id in result]
        ### End your code

通过一个简单的查询来测试索引在真实数据集上是否正常工作。

In [142]:
BSBI_instance = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir",
)
BSBI_instance.retrieve("boolean retrieval")

[46542, 7451]
[[5681, 6812, 6822, 9368, 9398, 9566, 10089, 10090, 10144, 10551, 10552, 10566, 10952, 10953, 11204, 11491, 12973, 16171, 19931, 21188, 21503, 23284, 23359, 23932, 25197, 25746, 27589, 27919, 27941, 27972, 27974, 28704, 29399, 29469, 29478, 29496, 29518, 29701, 30090, 30385, 30431, 30555, 30593, 30730, 30733, 30768, 30822, 31201, 31217, 31219, 31320, 31339, 31419, 31420, 31469, 31490, 31524, 35602, 35605, 35609, 35617, 35628, 35744, 37236, 43926, 43934, 43937, 43939, 43943, 43950, 43960, 43975, 43986, 44002, 44003, 44008, 44011, 44024, 44032, 44036, 44037, 44049, 44053, 44054, 44056, 44086, 44091, 44097, 44101, 44127, 44128, 44136, 44139, 44148, 44150, 44151, 44152, 44153, 44156, 44157, 44180, 44181, 44183, 44186, 44190, 44355, 48720, 48944, 49688, 49728, 49729, 49737, 49806, 49815, 49818, 49819, 49823, 49833, 49834, 49835, 49840, 49849, 49851, 49874, 50065, 50067, 50713, 51970, 51971, 52607, 55507, 55510, 55519, 55523, 55531, 55532, 55534, 57739, 57742, 58071, 58170, 595

['0\\acomp.stanford.edu_jobs_technical_support_specialist',
 '0\\airlab.stanford.edu_workshops_june2011presentations_Asier_June2011OpenHouse.pdf',
 '0\\arcade.stanford.edu_arcade-journals',
 '0\\blogs.law.stanford.edu_robotics_2012_03_16_technological-rationality-the-logos-of-slavery-or-the-enabler-of-humane-progress_',
 '0\\bmir.stanford.edu_pages_view.php_national_center_for_biomedical_ontology_ncbo_receives_funding_through_2015',
 '0\\bmir.stanford.edu_people_view.php_4368',
 '0\\bmir.stanford.edu_people_view.php_lawrence_m_fagan',
 '0\\bmir.stanford.edu_people_view.php_mark_a_musen_',
 '0\\bmir.stanford.edu_people_view.php_martin_j_oconnor',
 '0\\bmir.stanford.edu_people_view.php_natasha_f_noy',
 '0\\bmir.stanford.edu_people_view.php_nigam_h_shah',
 '0\\bmir.stanford.edu_people_view.php_saeed_hassanpour',
 '0\\bmir.stanford.edu_projects_view.php_sweetinfo',
 '0\\bmir.stanford.edu_publications_by_author.php_adrien_coulet',
 '0\\bmir.stanford.edu_publications_by_author.php_russ_cucin

你也可以通过读取文件来测试其中的页面是否真的包含了查询的terms

In [ ]:
with open("pa1-data/1/cs276.stanford.edu_", "r") as f:
    print(f.read())

测试dev queries（提前构建好的查询与结果）是否正确 (1%)

In [144]:
#TODO 到这里才知道 doc_id_map 要把 块路径也存进去作为 str
for i in range(1, 9):
    with open("dev_queries/query." + str(i)) as q:
        query = q.read()
        my_results = [os.path.normpath(path) for path in BSBI_instance.retrieve(query)]
        with open("dev_output/" + str(i) + ".out") as o:
            reference_results = [os.path.normpath(x.strip()) for x in o.readlines()]
            if my_results != reference_results:
                print(my_results)
                print(reference_results)
                print(i)
                print(query)
            assert my_results == reference_results, (
                "Results DO NOT match for query: " + query.strip()
            )
        print("Results match for query:", query.strip())

[380, 110]
[[3, 4, 5, 7, 8, 9, 11, 14, 15, 19, 29, 31, 54, 56, 95, 96, 97, 103, 108, 109, 113, 116, 122, 123, 124, 125, 130, 132, 135, 136, 137, 139, 140, 147, 148, 150, 151, 152, 153, 155, 156, 157, 158, 159, 161, 162, 165, 169, 170, 173, 175, 176, 178, 179, 180, 181, 182, 183, 191, 192, 193, 195, 197, 199, 201, 206, 208, 217, 218, 228, 240, 252, 253, 257, 262, 264, 265, 269, 273, 274, 275, 276, 277, 281, 282, 283, 288, 295, 300, 303, 311, 312, 313, 314, 319, 320, 322, 323, 326, 338, 339, 346, 348, 350, 352, 370, 379, 382, 384, 385, 389, 390, 415, 417, 500, 501, 502, 503, 504, 505, 506, 508, 509, 511, 514, 517, 525, 532, 533, 534, 539, 540, 542, 543, 545, 550, 553, 557, 559, 560, 561, 562, 574, 626, 631, 641, 645, 650, 653, 655, 670, 673, 674, 677, 687, 707, 722, 728, 732, 734, 746, 749, 752, 760, 761, 763, 771, 773, 774, 775, 776, 783, 784, 785, 787, 788, 806, 807, 815, 816, 825, 834, 839, 840, 843, 844, 845, 849, 855, 856, 857, 860, 861, 864, 865, 866, 868, 869, 870, 873, 878, 884, 

AssertionError: Results DO NOT match for query: we are

如果出现了错误，可以通过以下代码比较输出与正确结果的差异

In [145]:
set(my_results) - set(reference_results)

{'4\\politicalscience.stanford.edu_undergraduate-program_political-science-minor',
 '2\\founders.stanford.edu_',
 '2\\gender.stanford.edu_people_roberta-r-katz',
 '8\\www.stanford.edu_dept_EHS_prod_training_',
 '6\\studentaffairs.stanford.edu_gradadmissions_faq-general',
 '3\\kzsu.stanford.edu_stationinfo_join.php',
 '4\\nmtri.stanford.edu_access.htm',
 '9\\www.stanford.edu_group_amyblueaward_sel.html',
 '2\\gender.stanford.edu_events_international-womens-day-celebration-lunch',
 '6\\www-group.slac.stanford.edu_hr_fva_export.htm',
 '7\\www-ssrl.slac.stanford.edu_safety_aha_b137_aha-b137_room_110.pdf',
 '9\\www.stanford.edu_group_hepl_seminar_110830_Piau%2520.html',
 '4\\opera.stanford.edu_librettists_DAnnunzio.html',
 '8\\www.stanford.edu_class_ee380_fall-schedule-20052006.html',
 '6\\studentaffairs.stanford.edu_gradadmissions_programs_honors',
 '6\\studentaffairs.stanford.edu_registrar_faculty_evaluation-level-0405',
 '4\\pangea.stanford.edu_people_faculty_sarah-soule',
 '5\\skil.stan

In [146]:
set(reference_results) - set(my_results)

set()

确保你构建自己的查询来测试所有可能的边界情况，例如数据集中没有出现的terms，或者拖慢合并的频繁出现的terms。

# 索引压缩  (30%)

在这部分，你将使用可变长字节编码对索引进行压缩。（gap-encoding可选，对gap进行编码）

下面几个Python运算符可能对你有帮助

In [ ]:
# Remainder (modulo) operator %

print("10 % 2 = ", 10 % 2)
print("10 % 3 = ", 10 % 3)

# Integer division in Python 3 is done by using two slash signs

print("10 / 3 = ", 10 / 3)
print("10 // 3 = ", 10 // 3)

完成下面的`CompressedPostings`类，我们将用它来替换`UncompressedPostings`。关于如何使用gap-encoding和可变长字节编码，你可以参考老师课件或者[Chapter 5](https://nlp.stanford.edu/IR-book/pdf/05comp.pdf)。 (18%)

In [42]:
class CompressedPostings:
    # If you need any extra helper methods you can add them here
    ### Begin your code
    @staticmethod
    def encode_number(num):
        # bit_str = format(num, "8b")
        out = array.array("B")
        is_end_byte = True
        while num > 0:
            to_encode = num % 128 # 2^7 = 128
            num = num // 128
            to_encode = f"{to_encode:07b}"
            if is_end_byte:
                out.insert(0, int(f"0{to_encode}",base=2)) # 需要7位对齐
                is_end_byte = False
            else:
                out.insert(0, int(f"1{to_encode}",base=2)) 
        return out
    ### End your code

    @staticmethod
    def encode(postings_list):
        """Encodes `postings_list` using gap encoding with variable byte
        encoding for each gap

        Parameters
        ----------
        postings_list: List[int]
            The postings list to be encoded

        Returns
        -------
        bytes:
            Bytes reprsentation of the compressed postings list
            (as produced by `array.tobytes` function)
        """
        ### Begin your code
        # 先变成 gap 
        gap_list = [postings_list[0]] + \
                    [postings_list[i+1] - postings_list[i] for i in range(0, len(postings_list)-1) ]
        
        # 再编码
        result = array.array("B")
        for item in gap_list:
            encoded_item = CompressedPostings.encode_number(item)
            result += encoded_item
        return result.tobytes()
        ### End your code

    @staticmethod
    def decode(encoded_postings_list):
        """Decodes a byte representation of compressed postings list

        Parameters
        ----------
        encoded_postings_list: bytes
            Bytes representation as produced by `CompressedPostings.encode`

        Returns
        -------
        List[int]
            Decoded postings list (each posting is a docIds)
        """
        ### Begin your code
        result = []
        array_restore = array.array("B")
        array_restore.frombytes(encoded_postings_list)
        cur_decoded_num = 0
        for item in array_restore:
            value = item & 0b0111_1111
            cur_decoded_num = (cur_decoded_num << 7) | value # 并上去
            if item >> 7 == 0:
                # 最后一个字节一定是0 开头的
                result.append(cur_decoded_num + (result[-1] if len(result)>0 else 0)) # if else 三元运算符前面表达式得加括号，否则会尽可能延伸
                cur_decoded_num = 0
        return result
        ### End your code

首先，如果你实现了额外的辅助函数，写一些测试样例

In [29]:
### Begin your code
test_array = array.array("B")
test_array.append(int(f"0{4:07b}",base=2))
assert CompressedPostings.encode_number(4) == test_array

test_array2 = array.array("B")
# 11280 = "1011000_0010000"
part1 = "1011000"
part2 = "0010000"
test_array2.append(int(f"1{part1}", base=2))
test_array2.append(int(f"0{part2}", base=2))

assert CompressedPostings.encode_number(11280) == test_array2

# test encode
CompressedPostings.encode([2,3,4,5, 128])
### End your code

b'\x02\x01\x01\x01{'

我们实现了一个简单的函数来测试你编码的列表是否被正确解码

In [45]:
def test_encode_decode(l):
    e = CompressedPostings.encode(l)
    d = CompressedPostings.decode(e)
    assert d == l
    print(l, e)
    print(d)
test_encode_decode([2,3,4,235,2335,3546346])

[2, 3, 4, 235, 2335, 3546346] b'\x02\x01\x01\x81g\x904\x81\xd8\xa7K'
[2, 3, 4, 235, 2335, 3546346]


写一些测试样例来确保文档列表的压缩和解压正常运行 (2%)

In [ ]:
### Begin your code
#TODO
### End your code

现在让我们创建一个新的输出文件夹并使用`CompressedPostings`来构建压缩索引

In [ ]:
try:
    os.mkdir("output_dir_compressed")
except FileExistsError:
    pass

In [ ]:
BSBI_instance_compressed = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir_compressed",
    postings_encoding=CompressedPostings,
)
BSBI_instance_compressed.index()

In [ ]:
BSBI_instance_compressed = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir_compressed",
    postings_encoding=CompressedPostings,
)
BSBI_instance_compressed.retrieve("boolean retrieval")

像之前一样，用已构造好的查询语句来测试是否正常运行 (5%)

In [ ]:
for i in range(1, 9):
    with open("dev_queries/query." + str(i)) as q:
        query = q.read()
        my_results = [
            os.path.normpath(path) for path in BSBI_instance_compressed.retrieve(query)
        ]
        with open("dev_output/" + str(i) + ".out") as o:
            reference_results = [os.path.normpath(x.strip()) for x in o.readlines()]
            assert my_results == reference_results, (
                "Results DO NOT match for query: " + query.strip()
            )
        print("Results match for query:", query.strip())

请追加压缩前后的文件大小截图 (5%)

# 额外的编码方式 (10%)

通过补充`ECCompressedPostings`的`encode` 和 `decode`方法来实现一种额外的索引压缩方式。在我们课上学的就是**gamma-encoding** 。另外如果大家感兴趣的话也可以了解**Delta Encoding** ，[ALGORITHM SIMPLE-9](https://github.com/manning/CompressionAlgorithms#simple-9) 等。

你应该以多字节（而不是bits）来存储倒排记录表，因为索引的长度和位置都存的是字节信息。 (4%)

In [ ]:
class ECCompressedPostings:
    # If you need any extra helper methods you can add them here
    ### Begin your code

    ### End your code

    @staticmethod
    def encode(postings_list):
        """Encodes `postings_list`

        Parameters
        ----------
        postings_list: List[int]
            The postings list to be encoded

        Returns
        -------
        bytes:
            Bytes reprsentation of the compressed postings list
        """
        ### Begin your code

        ### End your code

    @staticmethod
    def decode(encoded_postings_list):
        """Decodes a byte representation of compressed postings list

        Parameters
        ----------
        encoded_postings_list: bytes
            Bytes representation as produced by `CompressedPostings.encode`

        Returns
        -------
        List[int]
            Decoded postings list (each posting is a docId)
        """
        ### Begin your code

        ### End your code

同上，写一些测试样例来确保代码正常运行 (3%)

In [ ]:
### Begin your code

### End your code

请追加压缩前后的文件大小截图 (3%)

# 作业提交

本次作业用时约3周，截止日期为2024.03.26。请大家在截止日期前将代码、实验报告（可单独撰写，也可整合在jupyter notebook中）一起提交到ir24fall@163.com，邮件和文件命名方式均为`学号_姓名_hw1`，如`1811412_戚晓睿_hw1.ipynb`